In [41]:
label_to_coordinates = {
    "1-1": (0, 0), "1-2": (0.6, 0), "1-3": (1.2, 0), "1-4": (1.8, 0), "1-5": (2.4, 0), "1-6": (3.0, 0),"1-7": (3.6, 0), "1-8": (4.2, 0), "1-9": (4.8, 0), "1-10": (5.4, 0), "1-11": (6.0, 0),
    "2-1": (0, 0.6), "2-11": (6.0, 0.6),
    "3-1": (0, 1.2), "3-11": (6.0, 1.2),
    "4-1": (0, 1.8), "4-11": (6.0, 1.8),
    "5-1": (0, 2.4), "5-11": (6.0, 2.4),
    "6-1": (0, 3.0), "6-2": (0.6, 3.0), "6-3": (1.2, 3.0), "6-4": (1.8, 3.0), "6-5": (2.4, 3.0),"6-6": (3.0, 3.0), "6-7": (3.6, 3.0), "6-8": (4.2, 3.0), "6-9": (4.8, 3.0), "6-10": (5.4, 3.0), "6-11": (6.0, 3.0),
    "7-1": (0, 3.6), "7-11": (6.0, 3.6),
    "8-1": (0, 4.2), "8-11": (6.0, 4.2),
    "9-1": (0, 4.8), "9-11": (6.0, 4.8),
    "10-1": (0, 5.4), "10-11": (6.0, 5.4),
    "11-1": (0, 6.0), "11-2": (0.6, 6.0), "11-3": (1.2, 6.0), "11-4": (1.8, 6.0), "11-5": (2.4, 6.0),"11-6": (3.0, 6.0), "11-7": (3.6, 6.0), "11-8": (4.2, 6.0), "11-9": (4.8, 6.0), "11-10": (5.4, 6.0), "11-11": (6.0, 6.0)
}
label_mapping = {
    '11': '1-1','10': '1-2','9': '1-3','8': '1-4','7': '1-5','6': '1-6','5': '1-7','4': '1-8','3': '1-9','2': '1-10','1': '1-11',
    '12': '2-1','30': '2-11',
    '13': '3-1','29': '3-11',
    '14': '4-1','28': '4-11',
    '15': '5-1','27': '5-11',
    '16': '6-1','17': '6-2','18': '6-3','19': '6-4','20': '6-5','21': '6-6','22': '6-7','23': '6-8','24': '6-9','25': '6-10','26': '6-11',
    '49': '7-1','31': '7-11',
    '48': '8-1','32': '8-11',
    '47': '9-1','33': '9-11',
    '46': '10-1','34': '10-11',
    '45': '11-1','44': '11-2','43': '11-3','42': '11-4','41': '11-5','40': '11-6','39': '11-7','38': '11-8','37': '11-9','36': '11-10','35': '11-11'
}

In [42]:
import pandas as pd
import numpy as np
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import StandardScaler
from tensorflow.keras.models import load_model
from tensorflow import keras
import tensorflow as tf
import joblib  # 用於保存模型
import json
from sklearn.model_selection import train_test_split

from sklearn.model_selection import StratifiedShuffleSplit
import time
from tensorflow.keras.callbacks import EarlyStopping
from sklearn.linear_model import SGDRegressor

In [43]:
selected_columns = ['Label',
                    'AP3_Distance (mm)',
                    'AP3_StdDev (mm)',
                    'AP1_Rssi', 'AP2_Rssi', 'AP3_Rssi', 'AP4_Rssi']  

scaler_columns = ['AP3_Distance (mm)',
                  'AP3_StdDev (mm)', 
                  'AP1_Rssi', 'AP2_Rssi', 'AP3_Rssi', 'AP4_Rssi',
                  'AP1_Distance_predicted', 'AP2_Distance_predicted','AP4_Distance_predicted']

label_column = 'Label'
target_column = 'Label'


#  'AP1_Rssi','AP2_Rssi','AP3_Rssi','AP4_Rssi'
# 'AP1_Distance (mm)','AP2_Distance (mm)','AP3_Distance (mm)','AP4_Distance (mm)',
# 'AP1_StdDev (mm)','AP2_StdDev (mm)','AP3_StdDev (mm)','AP4_StdDev (mm)',

In [44]:
dataamount_set = [5,10,20,40]
N_val_set = [1,2,4,8]

In [45]:
for dada in range(4):

    dataamount = dataamount_set[dada]
    N_val = N_val_set[dada]

    N_train = dataamount # 訓練集每個類別至少要有 N_train 筆資料
    test_val_ratio = 1  # 剩餘資料中，50% 作為驗證集，50% 作為測試集

    weekrepresent = [['0','0'],['0','1'],['1','2'],['2','3'],['3','4'],['4','5']]
    alldatadate = ['2024_12_21','2024_12_27','2025_01_03','2025_01_10','2025_02_28']
    number_of_week = len(alldatadate)

    ALL_model_loss = []
    ALL_model_accuracy = []
    ALL_model_mean_mde = []


    for mmm in range(10):

        ALL_trainingtime = []
        ALL_loss = []
        ALL_accuracy = []
        ALL_mean_mde = []

        for i in range(number_of_week):

            scaler = joblib.load(f'scaler_regressor_dnn_AP1&AP4_{mmm}.pkl')

            if i == 0:
                base_model_reg = joblib.load(f'regressor_model_AP1&AP4_{mmm}.pkl')
                base_model_dnn = load_model(f'regressor_dnn_AP1&AP4_{mmm}.h5')

            else: 
                # 儲存更新後的regressor and dnn model
                base_model_reg = joblib.load(f'regressor_model_{weekrepresent[i][0]}to{weekrepresent[i][1]}_{mmm}.pkl')
                base_model_dnn = load_model(f'regressor_dnn_{weekrepresent[i][0]}to{weekrepresent[i][1]}_{mmm}.h5')
        

            test_file_path = f"timestamp_allignment_Balanced_{alldatadate[i]}_rtt_logs.csv"  
            date_test = f"{alldatadate[i]}"
            data = pd.read_csv(test_file_path, usecols=selected_columns)


            # DNN transfer learnging 凍結所有層
            for layer in base_model_dnn.layers[:-1]:  # 除了最後一層 (Output Layer)
                layer.trainable = False

            # 確認哪些層可訓練
            base_model_dnn.summary()

            base_model_dnn.compile(optimizer=keras.optimizers.Adam(learning_rate=0.001),
                        loss='sparse_categorical_crossentropy',
                        metrics=['accuracy'])


            data_imputed = data.groupby(label_column).apply(
                lambda group: group.fillna(group.mean())
            ).reset_index()

            print("original data columns :")
            print(data_imputed.columns)


            reverse_label_mapping = {v: int(k) - 1 for k, v in label_mapping.items()}  # 讓數字標籤 -1

            y = data_imputed[target_column]

            y_numeric = y.map(reverse_label_mapping)
            y_numeric

            # 把label部分拿掉
            X = data_imputed.drop(columns=['level_1','Label'])

            # 轉為 DataFrame 方便操作
            data = pd.DataFrame(X)
            data['label'] = y_numeric  # 加入 label 欄位

            train_data_full = data.groupby('label', group_keys=False).sample(n=N_train, replace=False, random_state=42)
            train_data_full

            if N_val > 0:
                sss = StratifiedShuffleSplit(n_splits=1, test_size=N_val / N_train) # , random_state=42
                train_index, val_index = next(sss.split(train_data_full.drop(columns=['label']), train_data_full['label']))
                train_data = train_data_full.iloc[train_index]
                val_data = train_data_full.iloc[val_index]
                
            else:
                val_data = pd.DataFrame(columns=data.columns)  # 若沒有 validation data，建立空 DataFrame
                train_data = train_data_full

            # 剩下的資料（未被抽入 train_data_full 的部分）直接作為 test set
            remaining_data = data.drop(train_data_full.index)
            train_data

            # 訓練 regressor 並儲存
            # ap1_data = train_data[['AP1_Rssi', 'AP1_Distance (mm)']].dropna().rename(
            #     columns={'AP1_Rssi': 'Rssi', 'AP1_Distance (mm)': 'Distance'}
            # )

            # ap2_data = train_data[['AP2_Rssi', 'AP2_Distance (mm)']].dropna().rename(
            #     columns={'AP2_Rssi': 'Rssi', 'AP2_Distance (mm)': 'Distance'}
            # )

            ap3_data = train_data[['AP3_Rssi', 'AP3_Distance (mm)']].dropna().rename(
                columns={'AP3_Rssi': 'Rssi', 'AP3_Distance (mm)': 'Distance'}
            )

            # ap4_data = train_data[['AP4_Rssi', 'AP4_Distance (mm)']].dropna().rename(
            #     columns={'AP4_Rssi': 'Rssi', 'AP4_Distance (mm)': 'Distance'}
            # )

            train_data_reg = pd.concat([ap3_data], ignore_index=True)


            X_train_reg = train_data_reg[['Rssi']]
            y_train_reg = train_data_reg['Distance']

            # 重新訓練模型（fine tuning）
            model_reg_finetuned = base_model_reg
            model_reg_finetuned.partial_fit(X_train_reg, y_train_reg)

            # 檢查更新後的係數與截距
            print("更新後模型的係數：", model_reg_finetuned.coef_, "截距：", model_reg_finetuned.intercept_)

            

            ### train data
            train_data['AP1_Distance_predicted'] = np.nan
            train_data['AP2_Distance_predicted'] = np.nan
            # train_data['AP3_Distance_predicted'] = np.nan
            train_data['AP4_Distance_predicted'] = np.nan

            mask_ap1 = train_data['AP1_Rssi'].notna()
            train_data.loc[mask_ap1, 'AP1_Distance_predicted'] = model_reg_finetuned.predict(
                train_data.loc[mask_ap1, ['AP1_Rssi']].rename(columns={'AP1_Rssi': 'Rssi'})
            )

            mask_ap2 = train_data['AP2_Rssi'].notna()
            train_data.loc[mask_ap2, 'AP2_Distance_predicted'] = model_reg_finetuned.predict(
                train_data.loc[mask_ap2, ['AP2_Rssi']].rename(columns={'AP2_Rssi': 'Rssi'})
            )

            # mask_ap3 = train_data['AP3_Rssi'].notna()
            # train_data.loc[mask_ap3, 'AP3_Distance_predicted'] = model_reg_finetuned.predict(
            #     train_data.loc[mask_ap3, ['AP3_Rssi']].rename(columns={'AP3_Rssi': 'Rssi'})
            # )

            mask_ap4 = train_data['AP4_Rssi'].notna()
            train_data.loc[mask_ap4, 'AP4_Distance_predicted'] = model_reg_finetuned.predict(
                train_data.loc[mask_ap4, ['AP4_Rssi']].rename(columns={'AP4_Rssi': 'Rssi'})
            )

            ### val data
            val_data['AP1_Distance_predicted'] = np.nan
            val_data['AP2_Distance_predicted'] = np.nan
            # val_data['AP3_Distance_predicted'] = np.nan
            val_data['AP4_Distance_predicted'] = np.nan

            mask_ap1 = val_data['AP1_Rssi'].notna()
            val_data.loc[mask_ap1, 'AP1_Distance_predicted'] = model_reg_finetuned.predict(
                val_data.loc[mask_ap1, ['AP1_Rssi']].rename(columns={'AP1_Rssi': 'Rssi'})
            )

            mask_ap2 = val_data['AP2_Rssi'].notna()
            val_data.loc[mask_ap2, 'AP2_Distance_predicted'] = model_reg_finetuned.predict(
                val_data.loc[mask_ap2, ['AP2_Rssi']].rename(columns={'AP2_Rssi': 'Rssi'})
            )

            # mask_ap3 = val_data['AP3_Rssi'].notna()
            # val_data.loc[mask_ap3, 'AP3_Distance_predicted'] = model_reg_finetuned.predict(
            #     val_data.loc[mask_ap3, ['AP3_Rssi']].rename(columns={'AP3_Rssi': 'Rssi'})
            # )

            mask_ap4 = val_data['AP4_Rssi'].notna()
            val_data.loc[mask_ap4, 'AP4_Distance_predicted'] = model_reg_finetuned.predict(
                val_data.loc[mask_ap4, ['AP4_Rssi']].rename(columns={'AP4_Rssi': 'Rssi'})
            )

            ### remaining data
            remaining_data['AP1_Distance_predicted'] = np.nan
            remaining_data['AP2_Distance_predicted'] = np.nan
            # remaining_data['AP3_Distance_predicted'] = np.nan
            remaining_data['AP4_Distance_predicted'] = np.nan

            
            mask_ap1 = remaining_data['AP1_Rssi'].notna()
            remaining_data.loc[mask_ap1, 'AP1_Distance_predicted'] = model_reg_finetuned.predict(
                remaining_data.loc[mask_ap1, ['AP1_Rssi']].rename(columns={'AP1_Rssi': 'Rssi'})
            )

            mask_ap2 = remaining_data['AP2_Rssi'].notna()
            remaining_data.loc[mask_ap2, 'AP2_Distance_predicted'] = model_reg_finetuned.predict(
                remaining_data.loc[mask_ap2, ['AP2_Rssi']].rename(columns={'AP2_Rssi': 'Rssi'})
            )

            # mask_ap3 = remaining_data['AP3_Rssi'].notna()
            # remaining_data.loc[mask_ap3, 'AP3_Distance_predicted'] = model_reg_finetuned.predict(
            #     remaining_data.loc[mask_ap3, ['AP3_Rssi']].rename(columns={'AP3_Rssi': 'Rssi'})
            # )

            mask_ap4 = remaining_data['AP4_Rssi'].notna()
            remaining_data.loc[mask_ap4, 'AP4_Distance_predicted'] = model_reg_finetuned.predict(
                remaining_data.loc[mask_ap4, ['AP4_Rssi']].rename(columns={'AP4_Rssi': 'Rssi'})
            )

            # 更新 DNN 模型用的特徵欄位，將 regressor 預測值加入
            # selected_columns_dnn = selected_columns + ['AP1_Distance_predicted', 'AP4_Distance_predicted']

            print("new added feature column: ")
            print(list(train_data.columns))

            # -------------------------------
            # 準備 DNN 模型的輸入
            # 這邊重點：保留 DataFrame 結構，依據 scaler_columns 選取正確欄位，再進行 scaler.transform
            # -------------------------------
            # 選取訓練、驗證、測試集中的 scaler_columns（順序需與訓練時一致）

            X_train_df = train_data[scaler_columns].copy()
            y_train = train_data['label'].values

            X_val_df = val_data[scaler_columns].copy()
            y_val = val_data['label'].values

            X_test_df = remaining_data[scaler_columns].copy()
            y_test = remaining_data['label'].values

            # 使用預先訓練的 scaler 進行標準化
            X_scaled_train = scaler.transform(X_train_df)
            X_scaled_val = scaler.transform(X_val_df)
            X_scaled_test = scaler.transform(X_test_df)

            # print("訓練資料數量：", len(X_scaled_train))
            # print("驗證資料數量：", len(X_scaled_val))
            # print("測試資料數量：", len(X_scaled_test))


            # **轉換為 NumPy 陣列**
            X_train, y_train = train_data.drop(columns=['label']).values, train_data['label'].values
            X_val, y_val = val_data.drop(columns=['label']).values, val_data['label'].values
            X_test, y_test = remaining_data.drop(columns=['label']).values, remaining_data['label'].values


            # **計算每個 Set 內各 Label 的資料數量**
            train_label_counts = pd.Series(y_train).value_counts().sort_index()
            val_label_counts = pd.Series(y_val).value_counts().sort_index()
            test_label_counts = pd.Series(y_test).value_counts().sort_index()

            # **確保所有 Labels 都有出現在三個 Set 裡**
            all_labels = sorted(set(train_label_counts.index) | set(val_label_counts.index) | set(test_label_counts.index))
            label_distribution = pd.DataFrame(index=all_labels)

            label_distribution["Training Set"] = train_label_counts
            label_distribution["Validation Set"] = val_label_counts
            label_distribution["Test Set"] = test_label_counts

            # **用 0 填補缺失值（表示該 Label 在該 Set 中沒有數據）**
            label_distribution = label_distribution.fillna(0).astype(int)

            from IPython.display import display
            display(label_distribution)

            start_time = time.time()

            if N_val > 0:
                early_stop = EarlyStopping(monitor='val_loss', patience=10, restore_best_weights=True)
                base_model_dnn.fit(X_scaled_train, y_train,
                                validation_data=(X_scaled_val, y_val),
                                epochs=10000, batch_size=min(32, max(8, len(X_scaled_train) // 2)),
                                callbacks=[early_stop])
            else:
                early_stop = EarlyStopping(monitor='loss', patience=10, restore_best_weights=True)
                base_model_dnn.fit(X_scaled_train, y_train,
                                epochs=10000, batch_size=min(32, max(8, len(X_scaled_train) // 2)),
                                callbacks=[early_stop])

            end_time = time.time()

            training_time = end_time - start_time
            # print(f"訓練時間：{training_time:.2f} 秒")
            

            # Accuracy
            loss, accuracy = base_model_dnn.evaluate(X_scaled_test, y_test)
            # print(f"Evaluation on 90% unused data - Loss: {loss:.4f}, Accuracy: {accuracy:.4f}")


        # MDE
            # 預測測試資料
            y_test_pred_numeric = base_model_dnn.predict(X_scaled_test)
            y_pred_classes = np.argmax(y_test_pred_numeric, axis=1)

            # 轉換為原本的 Label
            y_test_pred_labels = [label_mapping[str(num + 1)] for num in y_pred_classes]  # 補回 +1

            # 讀取測試資料的實際 Label
            y_test_actual = [label_mapping[str(num + 1)] for num in y_test]  # 補回 +1

            # 取得預測與實際座標
            y_test_pred_coordinates = np.array([label_to_coordinates[label] for label in y_test_pred_labels])
            y_test_actual_coordinates = np.array([label_to_coordinates[label] for label in y_test_actual])

            # 計算 MDE (Mean Distance Error)
            distances = np.linalg.norm(y_test_pred_coordinates - y_test_actual_coordinates, axis=1)
            mean_mde = np.mean(distances)

            # 記錄每個 RP 的 MDE
            mde_report_test = {}
            for true_label, distance in zip(y_test_actual, distances):
                if true_label not in mde_report_test:
                    mde_report_test[true_label] = []
                mde_report_test[true_label].append(distance)

            # 計算測試資料的 MDE 平均值
            mde_report_test_avg = {label: {"mde": np.mean(dists), "count": len(dists)} for label, dists in mde_report_test.items()}


            # 儲存更新後的regressor and dnn model
            joblib.dump(model_reg_finetuned,f'regressor_model_{weekrepresent[i+1][0]}to{weekrepresent[i+1][1]}_{mmm}.pkl')
            base_model_dnn.save(f'regressor_dnn_{weekrepresent[i+1][0]}to{weekrepresent[i+1][1]}_{mmm}.h5')

        
            # 內層迴圈結束後，只存這一次的最佳結果
            # ALL_trainingtime.append()
            ALL_mean_mde.append(mean_mde)
            ALL_loss.append(loss)
            ALL_accuracy.append(accuracy)

        ALL_model_accuracy.append(ALL_accuracy)
        ALL_model_loss.append(ALL_loss)
        ALL_model_mean_mde.append(ALL_mean_mde)

    output_lines = []

    # 印出每個模型
    for count, (m, n, p) in enumerate(zip(ALL_model_loss, ALL_model_accuracy, ALL_model_mean_mde)):
        output_lines.append(f"model_{count}")

        output_lines.append("Loss")
        line = "[" + ", ".join(f"{l:.4f}" for l in m) + "]"
        output_lines.append(line)

        output_lines.append("Accuracy")
        line = "[" + ", ".join(f"{a:.4f}" for a in n) + "]"
        output_lines.append(line)

        output_lines.append("MDE")
        line = "[" + ", ".join(f"{sasa:.4f}" for sasa in p) + "]"
        output_lines.append(line)

        output_lines.append(" ")  # 空行

    # 計算平均
    loss_arr = np.array(ALL_model_loss)
    acc_arr = np.array(ALL_model_accuracy)
    mde_arr = np.array(ALL_model_mean_mde)

    loss_avg = np.mean(loss_arr, axis=0)
    acc_avg = np.mean(acc_arr, axis=0)
    mde_avg = np.mean(mde_arr, axis=0)

    output_lines.append("Average Loss")
    output_lines.append("[" + ", ".join(f"{v:.4f}" for v in loss_avg) + "]")

    output_lines.append("Average Accuracy")
    output_lines.append("[" + ", ".join(f"{v:.4f}" for v in acc_avg) + "]")

    output_lines.append("Average MDE")
    output_lines.append("[" + ", ".join(f"{v:.4f}" for v in mde_avg) + "]")

    # 印出到螢幕
    for line in output_lines:
        print(line)

    # 存檔到文字檔
    with open(f"model_metrics_{dada}.txt", "w") as f:
        for line in output_lines:
            f.write(line + "\n")



Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ dense (Dense)                   │ (None, 128)            │         1,280 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization             │ (None, 128)            │           512 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout (Dropout)               │ (None, 128)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_1 (Dense)                 │ (None, 256)            │        33,024 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_1           │ (None, 256)            │         1,024 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_1 (Dropout)             │ (None, 256)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_2 (Dense)                 │ (None, 128)            │        32,896 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization_2           │ (None, 128)            │           512 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_2 (Dropout)             │ (None, 128)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_3 (Dense)                 │ (None, 49)             │         6,321 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 75,571 (295.20 KB)

 Trainable params: 6,321 (24.69 KB)

 Non-trainable params: 69,248 (270.50 KB)

...

original data columns :
Index(['Label', 'level_1', 'AP3_Distance (mm)', 'AP1_Rssi', 'AP2_Rssi',
       'AP3_Rssi', 'AP4_Rssi', 'AP3_StdDev (mm)'],
      dtype='object')
更新後模型的係數： [-51.22266515] 截距： [-421.93740877]
new added feature column: 
['AP3_Distance (mm)', 'AP1_Rssi', 'AP2_Rssi', 'AP3_Rssi', 'AP4_Rssi', 'AP3_StdDev (mm)', 'label', 'AP1_Distance_predicted', 'AP2_Distance_predicted', 'AP4_Distance_predicted']


C:\Users\吳定洋\AppData\Local\Temp\ipykernel_6420\4089642212.py:128: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train_data['AP1_Distance_predicted'] = np.nan
C:\Users\吳定洋\AppData\Local\Temp\ipykernel_6420\4089642212.py:129: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train_data['AP2_Distance_predicted'] = np.nan
C:\Users\吳定洋\AppData\Local\Temp\ipykernel_6420\4089642212.py:131: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer

Training Set  Validation Set  Test Set
0             32               8       366
1             32               8       366
2             32               8       366
3             32               8       366
4             32               8       366
5             32               8       366
6             32               8       366
7             32               8       366
8             32               8       366
9             32               8       366
10            32               8       366
11            32               8       366
12            32               8       366
13            32               8       366
14            32               8       366
15            32               8       366
16            32               8       366
17            32               8       366
18            32               8       366
19            32               8       366
20            32               8       366
21            32               8       366
22            32               8       366
23            32               8       366
24            32               8       366
25            32               8       366
26            32               8       366
27            32               8       366
28            32               8       366
29            32               8       366
30            32               8       366
31            32               8       366
32            32               8       366
33            32               8       366
34            32               8       366
35            32               8       366
36            32               8       366
37            32               8       366
38            32               8       366
39            32               8       366
40            32               8       366
41            32               8       366
42            32               8       366
43            32               8       366
44            32               8       366
45            32               8       366
46            32               8       366
47            32               8       366
48            32               8       366

Epoch 1/10000
49/49 ━━━━━━━━━━━━━━━━━━━━ 1s 6ms/step - accuracy: 0.1709 - loss: 5.8667 - val_accuracy: 0.2781 - val_loss: 3.7893
Epoch 2/10000
49/49 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step - accuracy: 0.2857 - loss: 4.0539 - val_accuracy: 0.4031 - val_loss: 2.5246
Epoch 3/10000
49/49 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step - accuracy: 0.3168 - loss: 3.1356 - val_accuracy: 0.5026 - val_loss: 1.7253
Epoch 4/10000
49/49 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step - accuracy: 0.3810 - loss: 2.4582 - val_accuracy: 0.6071 - val_loss: 1.2148
Epoch 5/10000
49/49 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step - accuracy: 0.4569 - loss: 1.8150 - val_accuracy: 0.7143 - val_loss: 0.9029
Epoch 6/10000
49/49 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step - accuracy: 0.5321 - loss: 1.6571 - val_accuracy: 0.7781 - val_loss: 0.6639
Epoch 7/10000
49/49 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step - accuracy: 0.6140 - loss: 1.3154 - val_accuracy: 0.8469 - val_loss: 0.5244
Epoch 8/10000
49/49 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step - accuracy: 0.6318 - loss: 1.1960 - val_accu

model_0
Loss
[0.2011, 0.1776, 0.2336, 0.2282, 0.1391]
Accuracy
[0.9469, 0.9512, 0.9364, 0.9351, 0.9653]
MDE
[0.1301, 0.1157, 0.1431, 0.1379, 0.0660]
 
model_1
Loss
[0.1886, 0.2005, 0.2353, 0.3189, 0.1515]
Accuracy
[0.9491, 0.9448, 0.9360, 0.9229, 0.9630]
MDE
[0.1234, 0.1287, 0.1390, 0.1686, 0.0692]
 
model_2
Loss
[0.2306, 0.2426, 0.2535, 0.2733, 0.1825]
Accuracy
[0.9398, 0.9397, 0.9308, 0.9307, 0.9604]
MDE
[0.1481, 0.1360, 0.1495, 0.1458, 0.0776]
 
model_3
Loss
[0.2098, 0.1899, 0.2528, 0.2564, 0.1461]
Accuracy
[0.9445, 0.9505, 0.9328, 0.9295, 0.9639]
MDE
[0.1395, 0.1137, 0.1428, 0.1515, 0.0640]
 
model_4
Loss
[0.2008, 0.1865, 0.2263, 0.2228, 0.1790]
Accuracy
[0.9469, 0.9494, 0.9365, 0.9395, 0.9588]
MDE
[0.1346, 0.1185, 0.1371, 0.1264, 0.0766]
 
model_5
Loss
[0.1974, 0.2005, 0.2425, 0.2597, 0.1406]
Accuracy
[0.9458, 0.9482, 0.9371, 0.9300, 0.9652]
MDE
[0.1370, 0.1152, 0.1411, 0.1451, 0.0634]
 
model_6
Loss
[0.2092, 0.1956, 0.2307, 0.2676, 0.1441]
Accuracy
[0.9442, 0.9470, 0.9368, 0.9312